# Load Data

In [8]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

from sklearn.model_selection import train_test_split

from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
from sklearn.feature_selection import SelectFromModel

import pickle

# load dataset
# data = pd.read_csv('D:/OneDrive - 한동대학교/PROJECT/트머프로젝트/Data/BTC_train.csv')
data = pd.read_csv('D:/OneDrive - 한동대학교/PROJECT/트머프로젝트/output/BTC_sum_plus_nn_features.csv')

# train dataset도 nn을 과거에서만 가져온다. test dataset은 nn을 과거에서만 가져온다.


# In practice, feature selection should be done after data pre-processing,
# so ideally, all the categorical variables are encoded into numbers,
# and then you can assess how deterministic they are of the target

# here for simplicity I will use only numerical variables
# select numerical columns:

numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
numerical_vars = list(data.select_dtypes(include=numerics).columns)
data = data[numerical_vars]

In [9]:
print(data.shape) # Check the shape of NN file.

pd.set_option('display.max_columns', None)
data.head(3)

(74280, 18242)


realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000105    2.575188      -0.000089        0.001815   
1                   0.000107    2.557507      -0.000089        0.001815   
2                   0.000106    2.562293       0.000000        0.001815   

   high_low_gap  trade_vol   end_price  BB_width_w20  BB_width_w40  \
0      0.001904   1.138501  22599000.0  48144.956559  47257.071103   
1      0.001904   1.100893  22596000.0  50564.809898  50311.440306   
2      0.001815   1.124306  22599000.0  53873.536126  53013.302636   

   BB_width_w10  dv1_realized_volatility  dv5_realized_volatility_mean0  \
0  55194.202594                 0.000154                       0.000154   
1  54273.382058                 0.000156                       0.000156   
2  51861.353627                 0.000159                       0.000159   

   dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
0          -0.000310            0.001238                       0.000046   
1          -0.000177            0.001371                       0.000077   
2          -0.000044            0.001238                       0.000140   

   num_trades_150  lowest_return_150  highest_return_150  high_low_gap_150  \
0              85          -0.000089            0.000089          0.000177   
1              68          -0.000089            0.000354          0.000443   
2              69           0.000000            0.000354          0.000354   

   trade_vol_150  realized_volatility_mean0_300  num_trades_300  \
0       3.814411                       0.000100             147   
1       1.921894                       0.000106             126   
2       2.159312                       0.000109             125   

   lowest_return_300  highest_return_300  high_low_gap_300  trade_vol_300  \
0          -0.000089            0.000354          0.000443       5.543539   
1          -0.000089            0.000399          0.000487       3.760741   
2           0.000000            0.000753          0.000753       4.498119   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000092             209          -0.000089   
1                       0.000116             259          -0.000089   
2                       0.000119             286           0.000000   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.001284          0.001373       9.178568   -2.503398   
1            0.001815          0.001904       9.098996   -2.887379   
2            0.001815          0.001815       9.661851   -2.787476   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_5  \
0   -2.492577   -2.457350    -2.437520    -2.411095  0.001029   
1   -2.786359   -2.687438    -2.633461    -2.614329  0.000948   
2   -2.785780   -2.635687    -2.586336    -2.562354  0.000952   

   bidask_spread_0  bidask_spread_1  liq_last_1_150  liq_last_2_150  \
0         2.030769        10.261539        0.001555        0.001703   
1         2.098361        13.000000        0.000299        0.000458   
2         1.487500         9.412500        0.000284        0.001064   

   liq_last_5_150  liq_last_10_150  liq_last_15_150  bidask_spread_0_150  \
0        0.002171         0.002716         0.003101             2.000000   
1        0.000700         0.001334         0.001723             5.636363   
2        0.001406         0.001930         0.002127             6.533333   

   bidask_spread_1_150  liq_last_1_300  liq_last_2_300  liq_last_5_300  \
0             9.000000        0.000238        0.000819        0.002223   
1             9.000000        0.001734        0.002134        0.002249   
2             8.533334        0.000070        0.000121        0.000282   

   liq_last_10_300  liq_last_15_300  bidask_spread_0_300  bidask_spread_1_300  \
0         0.003171         0.003458             6.061539             8.061539   
1         0.002762         0.003344             2.07

# Remove Row Data to Selection

In [14]:
target_var = 'dv5_realized_volatility_mean0'

print("Before remove target_var's threshold : " , data.shape)

# 'dv1_realized_volatility' 열의 25%와 75% 백분위수 계산 => dv5
percentile_25 = data[target_var].quantile(0.25)
percentile_75 = data[target_var].quantile(0.75)

# 0~25%와 75~100% 범위 밖의 행 제거
data_q1q4 = data[(data[target_var] <= percentile_25) | (data[target_var] >= percentile_75)]

print("After remove target var's threshold : " , data_q1q4.shape)

Before remove target_var's threshold :  (74280, 18242)
After remove target var's threshold :  (37140, 18242)


In [18]:
y = data_q1q4[target_var]
drop_list = ['dv1_realized_volatility','dv2_lowest_return','dv3_highest_return','dv4_realized_volatility_30s','dv5_realized_volatility_mean0']
drop_list.remove(target_var)
X = data_q1q4.drop(drop_list, axis=1)
# X = data_q1q4.drop(['realized_volatility', 'realized_volatility_150', 'realized_volatility_300', 'realized_volatility_450'], axis=1)

# Feature Selection (0)
## Remove Corrlative Features

In [19]:
def correlation(dataset, threshold, target_var):
    col_corr = set()  # Set of all the names of correlated columns
    corr_matrix = dataset.corr()
    
    for i in range(len(corr_matrix.columns)):
        if i % 10 == 0:
            print("progressed : ", (i/len(corr_matrix.columns)*100))        
        for j in range(i) :
            if (abs(corr_matrix.iloc[i, j]) > threshold) & (abs(corr_matrix.iloc[i, j]) < 1): # we are interested in absolute coeff value
                
                # Drop one of them with lower correlation with our target variable.
                if corr_matrix[target_var][i] >= corr_matrix[target_var][j]:
                    colname = corr_matrix.columns[j]  # getting the name of column
                elif corr_matrix[target_var][i] < corr_matrix[target_var][j]:
                    colname = corr_matrix.columns[i]  # getting the name of column        
                col_corr.add(colname)
                
    return col_corr

# note that we reduce the correlation threshold
# to remove more features
corr_features = correlation(X.sample(n=2000, random_state=42), 0.9, target_var)
print('correlated features: ', len(set(corr_features)) )

progressed :  0.0
progressed :  0.0548305735277991
progressed :  0.1096611470555982
progressed :  0.1644917205833973
progressed :  0.2193222941111964
progressed :  0.2741528676389955
progressed :  0.3289834411667946
progressed :  0.3838140146945937
progressed :  0.4386445882223928
progressed :  0.4934751617501919
progressed :  0.548305735277991
progressed :  0.6031363088057901
progressed :  0.6579668823335892
progressed :  0.7127974558613883
progressed :  0.7676280293891874
progressed :  0.8224586029169865
progressed :  0.8772891764447855
progressed :  0.9321197499725847
progressed :  0.9869503235003838
progressed :  1.041780897028183
progressed :  1.096611470555982
progressed :  1.1514420440837811
progressed :  1.2062726176115801
progressed :  1.2611031911393793
progressed :  1.3159337646671785
progressed :  1.3707643381949777
progressed :  1.4255949117227766
progressed :  1.4804254852505758
progressed :  1.5352560587783748
progressed :  1.590086632306174
progressed :  1.6449172058339

In [20]:
# Set을 List로 변환
corr_features = list(corr_features)

# List를 Pickle로 저장
with open('corr_list_2.pkl', 'wb') as f:
    pickle.dump(corr_features, f)

# 저장된 Pickle 파일을 로드하는 방법
with open('corr_list_2.pkl', 'rb') as f:
    corr_features = pickle.load(f)

print(len(corr_features))

12642


In [21]:
# correlation 이 다른 변수와 높은 변수는 삭제한다.
X.drop(labels=corr_features, axis=1, inplace=True)

# target var 도 이제 제거한다.
X.drop(target_var, axis=1, inplace=True)

In [22]:
X.shape

(37140, 5595)

# Feature Selction A (This one is currently working for too long.)

## Exhaustive Feature Selection

This exhaustive feature selection algorithm is a wrapper approach for brute-force evaluation of feature subsets; the best subset is selected by optimizing a specified performance metric given an arbitrary regressor or classifier.

In [23]:
import pandas as pd

from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import roc_auc_score, r2_score
from sklearn.model_selection import train_test_split

from mlxtend.feature_selection import ExhaustiveFeatureSelector as EFS

In [18]:
# 이 코드는 거의 안 돌아간다고 보면 된다. RTX3080으로 10000시간 돌았는데 안 끝남.

# exhaustive search

# in order to shorter search time for the demonstration
# i will ask the algorithm to try all possible 10 and 11
# feature combinations

# if you have access to a multicore or distributed computer
# system you can try more greedy searches

efs = EFS(RandomForestRegressor(n_estimators=5,
                                n_jobs=4,
                                random_state=0,
                                max_depth=2),
          min_features=1,
          max_features=2,
          scoring='r2',
          print_progress=True,
          cv=2)

efs = efs.fit(X, y)

KeyboardInterrupt: 

In [ ]:
data.columns[list(efs.best_idx_)]

# Feature Selction B

## Embedded Methods: Linear Model Coefficients

train a Linear regression model and select features with higher coefficients.

In [24]:
# the features in the house dataset are in different scales
# so we train a scaler to scale them

scaler = StandardScaler()
scaler.fit(X)

# the LinearRegression object from sklearn is a non-regularised
# linear method. It fits by matrix multiplication and not 
# gradient descent.
# therefore we don't need to specify penalty and other parameters

sel_ = SelectFromModel(LinearRegression())

sel_.fit(scaler.transform(X), y)

# let's count the number of variables selected
selected_feat = X.columns[(sel_.get_support())]

# 저장할 파일 이름
file_name = "selected_feat_linear_coeff.pkl"

# selected_feat 변수를 pkl 파일로 저장
with open(file_name, 'wb') as file:
    pickle.dump(selected_feat, file)

print(f"{file_name} 파일이 저장되었습니다.")

print(len(selected_feat))


# and now, let's compare the  amount of selected features
# with the amount of features which coefficient is above the
# mean coefficient, to make sure we understand the output of
# sklearn

print('total features: {}'.format((X.shape[1])))

print('selected features: {}'.format(len(selected_feat)))

print(
    'features with coefficients greater than the mean coefficient: {}'.format(
        np.sum(
            np.abs(sel_.estimator_.coef_) > np.abs(
                sel_.estimator_.coef_).mean())))

selected_feat_linear_coeff.pkl 파일이 저장되었습니다.
1369
total features: 5595
selected features: 1369
features with coefficients greater than the mean coefficient: 1369


In [25]:
selected_feat

Index(['lowest_return_150', 'highest_return_150', 'high_low_gap_150',
       'realized_volatility_mean0_nn2_tvpl_c_mean',
       'realized_volatility_mean0_nn2_tvpl_epliq5_c_mean',
       'realized_volatility_mean0_nn2_BB_width_w10_c_mean',
       'realized_volatility_mean0_nn2_ep_liq_5_c_mean',
       'realized_volatility_mean0_nn2_liq_last_5_c_mean',
       'realized_volatility_mean0_nn2_liq_last_1_c_mean',
       'realized_volatility_mean0_nn2_highest_return_c_mean',
       ...
       'tvpl5_nn2_liq_last_5_m_p1_median', 'tvpl5_nn2_liq_last_1_m_p1_median',
       'tvpl5_nn2_trade_vol_m_p1_median',
       'tvpl5_nn2_lowest_return_m_p1_median',
       'tvpl5_nn2_realized_volatility_mean0_m_p2_median',
       'tvpl5_nn2_tvpl_epliq5_m_p2_median', 'tvpl5_nn2_ep_liq_5_m_p2_median',
       'tvpl5_nn2_liq_last_5_m_p2_median', 'tvpl5_nn2_trade_vol_m_p2_median',
       'tvpl5_nn4_tvpl_c_median'],
      dtype='object', length=1369)

# Feature Selction C

## Embedded Methods: Tree Importance

train a Linear regression model and select features with higher coefficients.

In [26]:
from sklearn.ensemble import RandomForestRegressor

In [27]:
# RandomForestRegressor 모델 학습
model = RandomForestRegressor(n_estimators=128, random_state=42, verbose=True)
model.fit(X, y)

# 특성 중요도 출력
feature_importances = model.feature_importances_
print("Feature Importances:", feature_importances)

# 특성 선택: 중요도가 높은 순서대로 특성 선택 (임계값 설정 가능)
selected_features_indices = feature_importances.argsort()[::-1]  # 중요도 내림차순 정렬
selected_features = X.columns[selected_features_indices]
print("Selected Features:", selected_features)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Feature Importances: [7.68613592e-04 1.58916980e-04 2.00229818e-04 ... 9.19696177e-05
 8.02622799e-05 1.31229522e-04]
Selected Features: Index(['dv5_realized_volatility_mean0_nn2_high_low_gap_m_p2_median',
       'dv5_realized_volatility_mean0_nn2_high_low_gap_m_p1_mean',
       'dv5_realized_volatility_mean0_nn2_high_low_gap_m_p2_mean',
       'dv5_realized_volatility_mean0_nn2_high_low_gap_m_p1_median',
       'dv5_realized_volatility_mean0_nn48_all_nn_m_p1_mean',
       'bidask_spread_1_nn64_all_nn_m_p1_mean',
       'dv5_realized_volatility_mean0_nn4_all_nn_m_p1_mean',
       'dv5_realized_volatility_mean0_nn4_high_low_gap_m_p2_mean',
       'dv5_realized_volatility_mean0_nn4_high_low_gap_m_p1_mean',
       'dv5_realized_volatility_mean0_nn64_sev_high_abs_nn_m_mean',
       ...
       'realized_volatility_30s_nn2_highest_return_m_p1_median',
       'liq_last_1_nn2_tvpl1_m_p2_median',
       'bidask_spread_0_nn2_tvpl_m_p2_median', 'trade_vol_nn2_tvpl_c_mean',
       'num_trades_nn2_

[Parallel(n_jobs=1)]: Done 128 out of 128 | elapsed: 424.3min finished


In [28]:
# 저장할 파일 이름
file_name = "selected_feat_ranfo.pkl"

# selected_feat 변수를 pkl 파일로 저장
with open(file_name, 'wb') as file:
    pickle.dump(selected_features, file)

print(f"{file_name} 파일이 저장되었습니다.")

print(len(selected_features))

selected_feat_ranfo.pkl 파일이 저장되었습니다.
5595


In [29]:
# 리스트를 DataFrame으로 변환
data = {'Name': list(selected_features), 'Importance': sorted(list(feature_importances), reverse=True)}
df = pd.DataFrame(data)

# DataFrame 출력
df.head(50)

Name  Importance
0   dv5_realized_volatility_mean0_nn2_high_low_gap...    0.126149
1   dv5_realized_volatility_mean0_nn2_high_low_gap...    0.117711
2   dv5_realized_volatility_mean0_nn2_high_low_gap...    0.109837
3   dv5_realized_volatility_mean0_nn2_high_low_gap...    0.106447
4   dv5_realized_volatility_mean0_nn48_all_nn_m_p1...    0.101023
5               bidask_spread_1_nn64_all_nn_m_p1_mean    0.017354
6   dv5_realized_volatility_mean0_nn4_all_nn_m_p1_...    0.014432
7   dv5_realized_volatility_mean0_nn4_high_low_gap...    0.011965
8   dv5_realized_volatility_mean0_nn4_high_low_gap...    0.009920
9   dv5_realized_volatility_mean0_nn64_sev_high_ab...    0.005249
10  dv5_realized_volatility_mean0_nn2_lowest_retur...    0.004559
11  dv5_realized_volatility_mean0_nn2_highest_retu...    0.004293
12  dv5_realized_volatility_mean0_nn2_lowest_retur...    0.004225
13  dv5_realized_volatility_mean0_nn2_highest_retu...    0.004050
14  dv5_realized_volatility_mean0_nn2_all_nn_m_p1_...    0.003050
15  dv5_realized_volatility_mean0_nn2_highest_retu...    0.002647
16  dv5_realized_volatility_mean0_nn2_all_nn_m_p1_...    0.002497
17    realized_volatility_mean0_nn64_all_nn_m_p1_mean    0.002484
18  dv5_realized_volatility_mean0_nn2_lowest_retur...    0.002414
19  realized_volatility_mean0_nn2_high_low_gap_m_p...    0.002377
20  dv5_realized_volatility_mean0_nn2_lowest_retur...    0.002357
21  dv5_realized_volatility_mean0_nn2_highest_retu...    0.002320
22  dv5_realized_volatility_mean0_nn2_highest_retu...    0.002292
23  dv5_realized_volatility_mean0_nn2_lowest_retur...    0.002232
24  dv5_realized_volatility_mean0_nn2_lowest_retur...    0.002220
25  dv5_realized_volatility_mean0_nn2_highest_retu...    0.002175
26  realized_volatility_mean0_nn2_high_low_gap_m_p...    0.002168
27  dv5_realized_volatility_mean0_nn4_all_nn_m_p2_...    0.001978
28  realized_volatility_mean0_nn2_high_low_gap_m_p...    0.001966
29  realized_volatility_mean0_nn2_high_low_gap_m_p...    0.001820
30  dv5_realized_volatility_mean0_nn4_bidask_sprea...    0.001725
31  dv5_realized_volatility_mean0_nn2_bidask_sprea...    0.001446
32  dv5_realized_volatility_mean0_nn4_highest_retu...    0.001376
33  dv5_realized_volatility_mean0_nn2_bidask_sprea...    0.001283
34  dv5_realized_volatility_mean0_nn48_sev_low_abs...    0.001282
35  dv5_realized_volatility_mean0_nn4_lowest_retur...    0.000980
36  dv5_realized_volatility_mean0_nn16_sev_low_abs...    0.000931
37  dv5_realized_volatility_mean0_nn64_sev_low_abs...    0.000775
38                                          end_price    0.000769
39  dv5_realized_volatility_mean0_nn4_lowest_retur...    0.000730
40  dv5_realized_volatility_mean0_nn32_sev_low_abs...    0.000697
41  dv5_realized_volatility_mean0_nn8_sev_low_abs_...    0.000684
42  dv5_realized_volatility_mean0_nn2_bidask_sprea...    0.000673
43  dv5_realized_volatility_mean0_nn2_bidask_sprea...    0.000643
44       bidask_spread_1_nn2_high_low_gap_m_p1_median    0.000619
45  dv5_realized_volatility_mean0_nn8_high_low_gap...    0.000605
46         bidask_spread_1_nn2_high_low_gap_m_p2_mean    0.000586
47  dv5_realized_volatility_mean0_nn16_sev_low_abs...    0.000578
48  dv5_realized_volatility_mean0_nn2_bidask_sprea...    0.000574
49  dv5_realized_volatility_mean0_nn4_bidask_sprea...    0.000566